# Importing all important libraries

In [8]:
import socket
import os
import threading
import yaml
import io
import math
# ML Specific
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from nltk.tokenize import RegexpTokenizer

# Initializing important variables

In [9]:
# Read YAML file
with open("config.yaml", 'r') as stream:
    config_loaded = yaml.safe_load(stream)

# reading from config file
port = config_loaded["server"]["port"]
datasets = config_loaded["datasets"]
s_nodes_count = config_loaded["kazaa"]["s_nodes"]
o_nodes_count = config_loaded["kazaa"]["o_node_per"]
all_nodes = s_nodes_count + (s_nodes_count*o_nodes_count)

In [10]:
# Global fields
lock = threading.Lock()
clientId = -1
threadCount = 0
node_threads = [None]*all_nodes
ports = []
ips = []
download_speed = [0]*all_nodes
gpu_ram_free = [0]*all_nodes
ram_free = [0]*all_nodes
cpu_free = [0]*all_nodes
cpu_cores = [0]*all_nodes
status = ['']*all_nodes
kazaa_constant = [0]*all_nodes
# format: snode_(ip,port,connection_object) as key : [(ip,port,connection)i] for i=onode_count as value 
network = {}

######################################## Connections ################################
# format: [connection_objects] for all nodes
connections = []
# format: [(ip, port, connection_object)i] for i = snode_count
snode_connections = []
node_connection = None

#### Formats:
Kazaa_constant = snode_(ip,port,connection_object) as key : [(ip,port,connection)i] for i=onode_count as value 

connections = [connection_objects] for all nodes

snode_connections = [(ip, port, connection_object)i] for i = snode_count

# Starting our main socket

In [11]:
# giving a dynamic IP and reuseable port to the server
port += 1
node_connection = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
node_connection.setsockopt(socket.SOL_SOCKET, socket.SO_REUSEADDR, 1)
host = socket.gethostname()
print("The server's IP address: ", socket.gethostbyname(host))
try:
    node_connection.bind((host, port))
except socket.error as e:
    print(str(e))
node_connection.listen(all_nodes)

# Write server host to config.yaml file
config_loaded["server"]["ip"] = socket.gethostbyname(host)
config_loaded["server"]["port"] = port
with io.open('config.yaml', 'w', encoding='utf8') as outfile:
    yaml.dump(config_loaded, outfile, default_flow_style=False, allow_unicode=True)

The server's IP address:  192.168.0.120


# Defining main functions required

In [12]:
# socket send consistent method 
# it sends the string, waits for the length of string client received, compares this length to the actual length. If both are equal
# it sends ack else, it resends the same txt again.
def socket_send(connection, txt):
    ack = False
    print(">> sending",txt+"...")
    while(not ack):
        connection.send(str.encode(txt))
        len_txt = int(connection.recv(1024).decode('utf-8'))
        if len_txt == len(txt):
            connection.send(str.encode("ack"))
            ack = True
        else:
            connection.send(str.encode("resending"))
    print(">> sent")

# socket receive consistent method 
# it receives the string, then sends its size back to the server and then it waits for an acknowledgement, If ack is received it 
# breaks out of the loop
def socket_rcv(connection, size=1024):
    ack = False
    while(not ack):
        txt = connection.recv(size).decode('utf-8')
        connection.send(str.encode(str(len(txt))))
        ack = True if connection.recv(size).decode('utf-8') == "ack" else False
    print(">> received", txt+"...")
    return txt
    
# giving minimum requirement of RAM for supernode
def get_required_ram(fileSize, node="s"):
    amount = fileSize/s_nodes_count
    if(node == "o"):
        amount /= o_nodes_count
    return amount
        
# calculating kazaa constant on the basis of which we are going to classify who is going to be a supernode or ordinary node
def cal_kazaa_constant(id):
    data_per_region = get_required_ram(size)
    # /10 means to get data downloaded in max 10 secs
    bytes_ps = data_per_region/10
    kazaa_constant[id] = (((gpu_ram_free[id]+ram_free[id] >= data_per_region)*0.5)
                          +(1 if (download_speed[id]/bytes_ps) >= 1 else (download_speed[id]/bytes_ps))*0.2
                          +((gpu_ram_free[id]/(max(gpu_ram_free) if max(gpu_ram_free) != 0 else 1))*0.15)
                          +((ram_free[id]/(max(ram_free) if max(ram_free) != 0 else 1))*0.075)
                          +((cpu_free[id]/100)*0.05)
                          +(1 if (cpu_cores[id]/8)>=1 else (cpu_cores[id]/8)*0.025)
                          )

# classifying nodes into supernode or ordinary node
def get_node_status(id):
    const = kazaa_constant[id]
    a = kazaa_constant.copy()
    a.sort()
    if const in a[len(a)-s_nodes_count:]:
        return "s"
    else:
        return "o"

# assigning onodes to supernodes
def create_network():
    d2_lst = []
    for i in range(len(ports)):
        lst = [ips[i], ports[i], status[i], kazaa_constant[i], connections[i]]
        d2_lst.append(lst)
    
    headers = ['IP', 'Port', 'Status', 'Kazaa Constant', 'Connection']
    df = pd.DataFrame(d2_lst, columns = headers)
    df = df.sort_values(by='Kazaa Constant', ascending=False)
    
    i = 0
    for index1, row1 in df[:s_nodes_count].iterrows():
        network[(row1['IP'], row1['Port'], row1['Connection'])] = []
        start = df.shape[0] - o_nodes_count*(i+1)
        end = df.shape[0] - o_nodes_count*i
        for index2, row2 in df[start:end].iterrows():
            network[(row1['IP'], row1['Port'], row1['Connection'])].append((row2['IP'], row2['Port'], row2['Connection']))
        i+=1


# cleaning the text of mails with respect to a tockenizer
def clean_str(string, reg = RegexpTokenizer(r'[a-z]+')):
    string = string.lower()
    tokens = reg.tokenize(string)
    return " ".join(tokens)

def send_rows_snode(connection, df, div, index, headers):
    socket_send(connection, "rcv:"+str(div))
    socket_send(connection, "rcv:"+headers)
    for i, row in df[int(div*index):int(div*(index+1))].iterrows():
        socket_send(connection, str(row[0])+":"+str(row[1])+":"+str(row[2])+":"+str(row[3]))
        ack = socket_rcv(connection)
        while(ack != "rcvd"):
            socket_send(connection, str(row[0])+":"+str(row[1])+":"+str(row[2])+":"+str(row[3]))
            ack = socket_rcv(connection)

# function to be run in independent thread
def multi_threaded_client(connection, id):
    socket_send(connection, 'Server is working:')
    
    # receiving system info
    data = socket_rcv(connection)
    if data.startswith("rcv:"):
        count = int(data[len("rcv:"):])
        if(count == 5):
            download_speed[id] = float(socket_rcv(connection)[len("dsp:"):])
            gpu_ram_free[id] = float(socket_rcv(connection)[len("gpu:"):])
            ram_free[id] = float(socket_rcv(connection)[len("ram:"):])
            cpu_free[id] = float(socket_rcv(connection)[len("cpu:"):])
            cpu_cores[id] = int(socket_rcv(connection)[len("cor:"):])

            # sending ack
            send_str = "ack: received following system info:  \nDownload_speed = " + str(download_speed[id]) + "B \nFree_GPU_RAM = " + str(gpu_ram_free[id]) + "B \nFree_RAM = " + str(ram_free[id]) + "B \nFree_CPU = " + str(cpu_free[id]) + " \nCPU_Cores = " + str(cpu_cores[id])
            socket_send(connection, send_str)
    lock.acquire()
    connections.append(connection)
    lock.release()

def most_frequent(List):
    return max(set(List), key = List.count)

"All defined"

'All defined'

# Getting a dataset value

In [13]:
# assuming dataset uploaded by the user
while(True):
    try:
        fileNumber = int(input("Which dataset you want to use from 0 - " + str(len(datasets)-1) + " : "))
        if fileNumber < str(len(datasets)):
            break
    except:
        pass
size = os.path.getsize(datasets[fileNumber]) 

Which dataset you want to use from 0 - 0 : 0


# Accepting connection from all nodes

accepting connection -> receiving count of parameters the nodes want to share -> receiving parameters -> sending an ack with all the received parameters

In [14]:
# always open for more clients to connect
print('Socket is listening..')
while(threadCount != all_nodes):
    Client, address = node_connection.accept()
    clientId += 1
    
    node_threads[threadCount] = threading.Thread(target = multi_threaded_client, args = (Client, clientId))
    node_threads[threadCount].start()
    
    threadCount += 1
    ips.append(address[0])
    ports.append(address[1])
    print('Thread Number: ' + str(threadCount) + " - " + 'Connected to: ' + address[0] + ':' + str(address[1]))

for thread in node_threads:
    thread.join()

Socket is listening..
>> sending Server is working:...
Thread Number: 1 - Connected to: 192.168.0.120:51690
>> sent
>> received rcv:5...
>> received dsp:1391093.7515555555...
>> received gpu:0...
>> received ram:8454008832...
>> received cpu:86.0...
>> received cor:4...
>> sending ack: received following system info:  
Download_speed = 1391093.7515555555B 
Free_GPU_RAM = 0.0B 
Free_RAM = 8454008832.0B 
Free_CPU = 86.0 
CPU_Cores = 4...
>> sent
>> sending Server is working:...
Thread Number: 2 - Connected to: 192.168.0.120:51782
>> sent
>> received rcv:5...
>> received dsp:1415195.9525768503...
>> received gpu:0...
>> received ram:8405819392...
>> received cpu:86.6...
>> received cor:4...
>> sending ack: received following system info:  
Download_speed = 1415195.9525768503B 
Free_GPU_RAM = 0.0B 
Free_RAM = 8405819392.0B 
Free_CPU = 86.6 
CPU_Cores = 4...
>> sent


# Initiating Kazaa

calculating kazaa_constant for all nodes -> fetching node status -> sending node status to the respective node -> creating a network from all the available nodes -> getting IP of each snode again -> sending this new IP to onodes in their respective region

In [17]:
# creates a nerwork of supernodes and ordinary nodes, and introduce them to each other
if(len(connections) >= all_nodes):
    #initiate_kazaa()
    for i in range(len(connections)):
        cal_kazaa_constant(i)
    
    print("Constants calculated are: ", kazaa_constant)
    
    for i in range(len(connections)):
        status[i] = get_node_status(i)
        
    print("Statuses calculated are: ", status)
        
    for connection in connections:
        send_str = "status:" + status[connections.index(connection)]
        socket_send(connection, send_str)
        send_str = "k_const:" + str(kazaa_constant[connections.index(connection)])
        socket_send(connection, send_str)
    
    # creating a network topology as in kazaa
    create_network()
    
    for (sIP, sPort, sConnection), onodes in network.items():
        onodes_IP_PORTS_to_send = len(onodes)
        snode_connections.append((sIP, sPort, sConnection))
        print("waiting to receive snodes ip:port to be shared among its region ordinary nodes...")
        ip_port = socket_rcv(sConnection).split(":")
        send_snode_IP_PORT = ip_port[0] + ":" + ip_port[1]
        print("rcvd: " + send_snode_IP_PORT)
        for (oIP, oPort, oConnection) in onodes:
            socket_send(oConnection, send_snode_IP_PORT)

Constants calculated are:  [0.8304999999999999, 0.8303724858973035]
Statuses calculated are:  ['s', 'o']
>> sending status:s...
>> sent
>> sending k_const:0.8304999999999999...
>> sent
>> sending status:o...
>> sent
>> sending k_const:0.8303724858973035...
>> sent
waiting to receive snodes ip:port to be shared among its region ordinary nodes...
>> received ubuntu:4345...
rcvd: ubuntu:4345
>> sending ubuntu:4345...
>> sent


# Ensemble Distribution

Reading the data -> cleaning the data -> Dividing the data into number of super nodes -> sending the data to respective supernodes

In [18]:
if(len(connections) >= all_nodes):
    # division, sending of dataset to supernodes, receiving predictions
    # ensemble_distribution()
    df = pd.read_csv('spam_ham_dataset.csv')
    df['text_clean'] = df['text'].apply(lambda string: clean_str(string))
    del df['text']
    
    # data per supernode
    division = math.ceil(df.shape[0]/s_nodes_count)
    
    # headers
    headers = ":".join(list(df.columns))
    
    index = 0
    print("Sending data...")
    for snode_connection in snode_connections:
        send_rows_snode(snode_connection[2], df, division, index, headers)
        print("Sent all data to", snode_connection[0], "at port", snode_connection[1])
        index += 1

Sending data...
>> sending rcv:5171...
>> sent
>> sending rcv:id:label:label_num:text_clean...
>> sent
>> sending 605:ham:0:subject enron methanol meter this is a follow up to the note i gave you on monday preliminary flow data provided by daren please override pop s daily volume presently zero to reflect daily activity you can obtain from gas control this change is needed asap for economics purposes...
>> sent
>> received rcvd...
>> sending 2349:ham:0:subject hpl nom for january see attached file hplnol xls hplnol xls...
>> sent
>> received rcvd...
>> sending 3624:ham:0:subject neon retreat ho ho ho we re around to that most wonderful time of the year neon leaders retreat time i know that this time of year is extremely hectic and that it s tough to think about anything past the holidays but life does go on past the week of december through january and that s what i d like you to think about for a minute on the calender that i handed out at the beginning of the fall semester the retrea

>> sent
>> received rcvd...
>> sending 4152:spam:1:subject roller coaster cigars for email loading brewster crude embody lignite cf aboard elisabeth doorkeep dichotomous chalkline keypunch pomp...
>> sent
>> received rcvd...
>> sending 3809:spam:1:subject get cheap via gra generic viagra at cheap prices most places charge we charge quite a difference right an amazing erection every time is guaranteed to you go into sexual overdrive today vroooom shipped to the whole world your solution is here http www getcheapdrugs biz via oxygen the link below is for people who hate spam http www getcheapdrugs biz off html...
>> sent
>> received rcvd...
>> sending 3217:ham:0:subject fw chevron phillips chemical co lp hplc sales buyback daren per your e mail to re your changing price for pricing errors as promised please see lee p s response below thanks tess original message from ray tess sent tuesday may am to meyers julie subject re chevron phillips chemical co lp hplc sales buyback importance high

>> sent
>> received rcvd...
>> sending 1832:ham:0:subject re cornhusker tenaska iv has been operating without a gas agency agreement since that portion of the transition agreement expired on august we met with sandy and the texas gas desk on september to firm up commercial terms which i think we generally accomplished for all matters other than the price that would be charged by the desk should we be concerned with the amount of time this is taking that is is there any risk we face bank wise or otherwise during the period of time before this agreement is inked and taken through the bank consent process rh forwarded by garrick hill hou ect on pm from sandi m braband on pm to john griffith corp enron enron cc garrick hill hou ect ect daren j farmer hou ect ect subject re cornhusker john i have a draft that i have been working on revising got pulled off to work on triple lutz again and may not have anything to distribute until late next week i will be out of the office on triple lutz the 

>> sent
>> received rcvd...
>> sending 1760:ham:0:subject duke cashout entries and here are the cashout entries for and july deal excess charge cashout total there is no purchase cashout for aug deal cashout excess charge total deal cashout thanks megan...
>> sent
>> received rcvd...
>> sending 23:ham:0:subject miscellaneous forwarded by ami chokshi corp enron on pm dscottl com on pm to ami chokshi corp enron enron cc subject miscellaneous sorry i m just now getting back to you here are some answers to your questions waskom is a field in east texas harrison county where we purchase gas from pennzenergy at the bryson c p and jeter wells the gas is termed up to new waskom gas gathering nwgg through june the term of the pennzenergy purchase we then buy the gas back from nwgg into our tetco east texas pool also termed up through virginia field used to be associated with ngpl but several years ago pennzenergy worked out a processing arrangement with corpus christi gas gathering so the gas i

>> sent
>> received rcvd...
>> sending 2365:ham:0:subject intraday eastrans nominations change for and nomination for please pass the following information to meagan parker her pricing isn t matching forwarded by marta k henderson houston pefs pec on am marta k henderson pm to dfarmer enron com john a bretz gcs cec pec pec cc john a bretz gcs cec pec pec donna j dobb houston pefs pec pec sharon beemer ftworth pefs pec pec subject intraday eastrans nominations change for and nomination for as follow up documentation for the intraday sale on the following states the pricing for the redeliveries mmbtu from fuels cotton valley priced per paragraph la of the contract price per mmbtu section in the transaction agreement mmbtu at etgs carthage hub tailgate priced per paragraph lc of the contract price per mmbtu section in the transaction agreement mmbtu at cipco mobile beaumont which is priced differently than paragraph lb of the contract price per mmbtu section in the transaction agreement t

...

>> sent
>> received rcvd...
>> sending 785:ham:0:subject customer meeting invitation good afternoon all i have attached the invitation to our th annual enron customer meeting to be held at the don ce sar in st pete s beach fl please feel free to fax or email to your customers as you see necessary but please use the rsvp forms for the trip they will be attending july or august the invitation attachement is generic and should be used for both rsvp forms the original invitation will be going out in the mail this evening with a requested return date of june if you have any questions or need an assistance please call me at x thank you heather choate...
>> sent
>> received rcvd...
>> sending 4968:spam:1:subject popular soft at low low prlces burch hi as one of our prefered custommers we d like to interest you are you looking for none expensjve high qualjty soft s for immediate down load we might have just what you need windows xp professional dolars adobe photoshop dolars microsoft office xp

>> received rcvd...
>> sending 1551:ham:0:subject re possibly adding deal prices to path manager from donna greif ect pm to patti sullivan hou ect ect victor lamadrid hou ect ect george smith hou ect ect pat clynes corp enron enron kevin heal cal ect ect cc diane h cook hou ect ect robert superty hou ect ect dave nommensen hou ect ect subject possibly adding deal prices to path manager please see note from nommensen below and let me know your thoughts note this additional functionality screen view may cause an impact on system performance thanks dg forwarded by donna greif hou ect on pm from dave nommensen am to donna greif hou ect ect cc matt pena na enron enron dave mcmullan hou ect ect subject possibly adding deal prices to path manager donna a request was brought up this week that i would like you to run by the managers for input add the deal price to the sales and supply list windows of path manager this seems more significant based on the transactions from eol this has been menti

>> sent
>> received rcvd...
>> sending 5037:spam:1:subject feel great in that magic moment you have not tried cialls yet than you cannot even imagine what it is like to be a real man in bed the thing is that a great errrectlon is provided for you exactly when you want cialis has a iot of advantaqes over viagra the effect lasts hours you are ready to start within just minutes you can mix it with alcohol we ship to any country denise...
>> sent
>> received rcvd...
>> sending 2514:ham:0:subject point change for deals oh yeah and that goes for deal crosstex also forwarded by mark mccoy corp enron on pm mark mccoy pm to elsa villarreal hou ect ect daren j farmer hou ect ect cc subject point change for deals ooops this is effective the lst forwarded by mark mccoy corp enron on pm mark mccoy pm to elsa villarreal hou ect ect daren j farmer hou ect ect cc subject point change for deals fyi i changed points on this deal from pgtt teco waha to pgtt teco katy for the nd let me know if you don t a

>> sent
>> received rcvd...
>> sending 4979:spam:1:subject penny stocks are about timing nomad international inc ndin a multi national internet communications company developing cost effective telecommunications through voice over internet protocol voip technologies shares outstanding oo float oo current price o wiil it continue higher watch this one friday as we know many of you like momentum breaking news may nomad international inc ndin commented today on the recent announcement by the canadian radio teievision and teiecommunications commission crtc that they would reguiate voice over internet protoco voip service only when it is provided and used as local telephone service in its decision the crtc determined that in an effort to buiid sustainable competition in ocal teiephone markets the incumbent carriers wiil not be permitted to price their local voip services below cost to stifie competition the ruling is a very positive one for nomad in our efforts to enter the canadian market 

KeyboardInterrupt: 

# X_Test Distribution

In [27]:
text = input("Write any text of an email to get classified:")
predictions = []
for snode_connection in snode_connections:
    socket_send(snode_connection[2], "rcv_test:"+text)
    # a word of either HAM or SPAM
    predictions.append(socket_rcv(snode_connection[2]))

print(most_frequent(predictions),"is your prediction for the above added email")


Write any text of an email to get classified:This is an email 
>> sending rcv_test:This is an email ...
>> sent
>> received spam...
>> sending rcv_test:This is an email ...


KeyboardInterrupt: 

In [28]:
network

{('192.168.0.120',
  51690,
  <socket.socket fd=61, family=AddressFamily.AF_INET, type=SocketKind.SOCK_STREAM, proto=0, laddr=('192.168.0.120', 4344), raddr=('192.168.0.120', 51690)>): [('192.168.0.120',
   51782,
   <socket.socket fd=64, family=AddressFamily.AF_INET, type=SocketKind.SOCK_STREAM, proto=0, laddr=('192.168.0.120', 4344), raddr=('192.168.0.120', 51782)>)]}